In [1]:
import sys
import time
import random
import datetime
import telepot
import requests
import json
import time
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By

In [2]:
token = 'YOUR BOT TOKEN COMES HERE' #put the bot token that you get after creating it, I used BotFather to create
driver = webdriver.Chrome(executable_path=r'PATH TO CHROME EXECUTABLE') #refer to selenium docs on how to use it
#you can even keep the driver hidden by using 'headless' functionality but keeping it visible enables you to see
#what is happening and how the code is working

In [3]:
def instagram_handling():
    homepage = "https://www.instagram.com/{YOUR USERNAME HERE}/" #this contains the url of your instagram account page
    driver.get(homepage)
    url = ""
    if check_login(driver) > -1: #checks if account is logged in
        print(driver.page_source.index("not-logged-in"))
        login(driver) #login if not already logged in
        url = driver.current_url
    else:
        print ("Already logged in")
        print (driver.current_url)
    driver.get(homepage + "saved") #now navigate to your saved page given by https://www.instagram.com/{YOUR USERNAME HERE}/saved
    time.sleep(2) #wait for 2 seconds for the page to load (might differ based on connectivity)
    elems = driver.find_elements_by_xpath("//a[@href]") #make a list of all the elements on the page having 'href'
    list=[]
    for elem in elems:
        list.append(elem.get_attribute("href")) #add their 'link' attributes to a list
    print (list)
    return list

#the returned list now contains all the links found on this page
#you can note that this link has 6 links unrelated to your post, but after that each link is a link to the post that you have saved


In [4]:
def check_login(driver):
    return driver.page_source.find("not-logged-in")
#on inspecting the html of the page before and after logging in, I noticed that there was a "not-logged-in" text in the header
#of the page before loggin in, which changed to "logged-in" after I log in
#that means if I am already logged in, a find("not-logged-in") on page source will return -1 as this text will not be present

In [5]:
def login(driver):
    timeout = 5
    driver.get("https://www.instagram.com/")
    try: # i wait till my needed elements are present on the page. refer to selenium docs for details.
        element_present = EC.presence_of_element_located((By.NAME, 'username'))
        WebDriverWait(driver, timeout).until(element_present)
    except TimeoutException:
        print ("Timed out waiting for page to load")
    username = driver.find_element_by_name("username")
    password = driver.find_element_by_name("password")

    username.send_keys("YOUR_USERNAME") #put your username
    password.send_keys("YOUR_PASSWORD") #put your password
    
    submit_button = driver.find_element_by_xpath("/html/body/div[1]/section/main/article/div[2]/div[1]/div/form/div[4]/button/div")
    #this is the default xpath of the submit button
    
    print(submit_button)
    submit_button.click() #login after entering fields
    try:
        element_present = EC.presence_of_element_located((By.ID, 'react-root'))
        WebDriverWait(driver, timeout).until(element_present)
    except TimeoutException:
        print ("Timed out waiting for page to load")
    time.sleep(5)
    print("Page loaded")

In [ ]:
#this is the telegram bot part
def handle(msg):
    chat_id = msg['chat']['id'] #get the user chat id 
    command = msg['text'][1:] #get the command text. used slicing as my commands are created starting with a '/' and I only 
                              #want the text which comes after it
    count = 0
    print ("Got command {}".format(command)) 
    if command == 'five':
        count = 5
    if command == 'last':
        count = 1
    if command == 'ten':
        count = 10
    #set my count based on command text
    if command == 'five' or command == 'ten' or command == 'last': #means I need to return the images
        #1st login
        bot.sendMessage(chat_id, "Logging in..")
        link_list = instagram_handling() #gets a list of links
        bot.sendMessage(chat_id, "Login success")
        bot.sendMessage(chat_id, "Getting last {} saved posts...".format(count))
        #then return array of last X posts
        for i in range(count):
            url=(link_list[i+7] + "media/?size=l") #I added 7 as I explained, the post links start from the 7th link
                                                 #after much trial and error and googling, I realized that just adding
                                                 #"media/?size=l" gives us a link to the full size image of the post
            driver.get(url)
            time.sleep(1)
            url = driver.current_url #the url changes after I visit the page. I need to now download the photo from this new url
            bot.sendPhoto(chat_id, url, disable_notification = True) #refer to telepot documentation
            #as of now this only works for images
            #i can add code to check if my link contains ".mp4" inside it. if that is true, then I can use the 
            #bot.sendVideo() method to directly return the video. I might add that in the future.
        bot.sendMessage(chat_id, "Done!")
    else:
        bot.sendMessage(chat_id, command) #if it is not a picture command, then just return the users text back to the user

bot = telepot.Bot(token) #this is the creation of bot. see any article on creating a basic "echo" bot which returns the 
                         #text the user has entered back to the user
bot.message_loop(handle)
print('I am listening ...')

while 1:
    time.sleep(10)

I am listening ...
Got command hey
Got command i
Got command 


Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\telepot\__init__.py", line 1158, in collector
    callback(item)
  File "<ipython-input-6-85a09c7871e1>", line 28, in handle
    bot.sendMessage(chat_id, command)
  File "c:\users\aman\lib\site-packages\telepot\__init__.py", line 513, in sendMessage
    return self._api_request('sendMessage', _rectify(p))
  File "c:\users\aman\lib\site-packages\telepot\__init__.py", line 491, in _api_request
    return api.request((self._token, method, params, files), **kwargs)
  File "c:\users\aman\lib\site-packages\telepot\api.py", line 155, in request
    return _parse(r)
  File "c:\users\aman\lib\site-packages\telepot\api.py", line 150, in _parse
    raise exception.TelegramError(description, error_code, data)
telepot.exception.TelegramError: ('Bad Request: message text is empty', 400, {'ok': False, 'error_code': 400, 'description': 'Bad Request: message text is empty'})


Got command 


Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\telepot\__init__.py", line 1158, in collector
    callback(item)
  File "<ipython-input-6-85a09c7871e1>", line 28, in handle
    bot.sendMessage(chat_id, command)
  File "c:\users\aman\lib\site-packages\telepot\__init__.py", line 513, in sendMessage
    return self._api_request('sendMessage', _rectify(p))
  File "c:\users\aman\lib\site-packages\telepot\__init__.py", line 491, in _api_request
    return api.request((self._token, method, params, files), **kwargs)
  File "c:\users\aman\lib\site-packages\telepot\api.py", line 155, in request
    return _parse(r)
  File "c:\users\aman\lib\site-packages\telepot\api.py", line 150, in _parse
    raise exception.TelegramError(description, error_code, data)
telepot.exception.TelegramError: ('Bad Request: message text is empty', 400, {'ok': False, 'error_code': 400, 'description': 'Bad Request: message text is empty'})


Got command 


...

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connection.py", line 160, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw
  File "c:\users\aman\lib\site-packages\urllib3\util\connection.py", line 61, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "c:\users\aman\lib\socket.py", line 748, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno 11001] getaddrinfo failed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 677, in urlopen
    chunked=chunked,
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 381, in _make_request
    self._validate_conn(conn)
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 976, in _validate_conn
    conn.connect()
  

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connection.py", line 160, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw
  File "c:\users\aman\lib\site-packages\urllib3\util\connection.py", line 61, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "c:\users\aman\lib\socket.py", line 748, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno 11001] getaddrinfo failed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 677, in urlopen
    chunked=chunked,
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 381, in _make_request
    self._validate_conn(conn)
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 976, in _validate_conn
    conn.connect()
  

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connection.py", line 160, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw
  File "c:\users\aman\lib\site-packages\urllib3\util\connection.py", line 61, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "c:\users\aman\lib\socket.py", line 748, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno 11001] getaddrinfo failed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 677, in urlopen
    chunked=chunked,
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 381, in _make_request
    self._validate_conn(conn)
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 976, in _validate_conn
    conn.connect()
  

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connection.py", line 160, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw
  File "c:\users\aman\lib\site-packages\urllib3\util\connection.py", line 61, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "c:\users\aman\lib\socket.py", line 748, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno 11001] getaddrinfo failed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 677, in urlopen
    chunked=chunked,
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 381, in _make_request
    self._validate_conn(conn)
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 976, in _validate_conn
    conn.connect()
  

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connection.py", line 160, in _new_conn
    (self._dns_host, self.port), self.timeout, **extra_kw
  File "c:\users\aman\lib\site-packages\urllib3\util\connection.py", line 61, in create_connection
    for res in socket.getaddrinfo(host, port, family, socket.SOCK_STREAM):
  File "c:\users\aman\lib\socket.py", line 748, in getaddrinfo
    for res in _socket.getaddrinfo(host, port, family, type, proto, flags):
socket.gaierror: [Errno 11001] getaddrinfo failed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 677, in urlopen
    chunked=chunked,
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 381, in _make_request
    self._validate_conn(conn)
  File "c:\users\aman\lib\site-packages\urllib3\connectionpool.py", line 976, in _validate_conn
    conn.connect()
  